# Asteroid Orbits
Part of Prof. Hanno Rein's ASTC02 course on Practical Astronomy. 
In this tutorial, we will read in two images of an asteroid and use those to estimate asteroid's orbit. This is part of your lab report. 

This notebook requires you to `pip install` the packages `rebound`, `numpy`, `matplotlib`, `emcee`, and `corner`.

In [ ]:
import rebound
import numpy as np
import emcee
import matplotlib.pyplot as plt
import corner

## Calculate the RA and Dec of the Asteroid
- Using Stellarium, use three (3) reference stars and calculate the RA and Dec of the asteroid.

What you need:
- The RA and Dec of three reference stars.
- The pixel location of the three reference stars in your two images.
- The pixel location of the asteroid in the image.
- The UTC time for both images of the asteroid.

Things to consider:
- Use RA and Dec in decimal format (instead of HH:MM:SS and degrees:arcmin:arcsec)
- **Quantify the uncertainty in RA and Dec of the asteroid.**
- **Where do the largest sources of uncertainty come from?**

In [ ]:
# These are example coordinated. You need to use your own!

ref_stars_RA_Dec = np.array([
       [[347.72920833,  14.17236111],
        [347.7655    ,  14.35922222],
        [348.00329167,  14.06913889]],

       [[347.72920833,  14.17236111],
        [347.7655    ,  14.35922222],
        [348.00329167,  14.06913889]]
])

ref_stars_pixel_loc = np.array([
       [[1469.97093173,  796.6773302 ],
        [ 795.30105846,  367.19079755],
        [1021.66897957, 1907.24475071]],

       [[1469.96779679,  795.88012025],
        [ 795.10491217,  367.09258461],
        [1020.99376574, 1907.98969892]]
])

asteroid_pixel_loc = np.array([
       [1731.67305417,  763.96463948],
       [1743.53776396,  750.19542396]
])

times = ['2022-08-11 03:14:10', '2022-08-11 04:26:06']

In [ ]:
def find_RA_Dec(object_pixel_loc, reference_star_pixel_loc, reference_star_ra_dec):
    '''
        Determines the RA and Dec of an object.
        It does this from the pixel coordinates of the object and 
          a set of reference stars along with the RA and Dec of the reference stars.
    '''
    
    # Unpack the RA, Dec, and pixel locations of the references stars and the object.
    obj_x, obj_y = object_pixel_loc
    ra, dec = np.array(reference_star_ra_dec).T
    cent_x, cent_y = np.array(reference_star_pixel_loc).T
    
    
    ### .... You need to implement this function
    
    
    # Calculate the RA and Dec of the object.
    ra = b1 + a11 * obj_x + a12 * obj_y
    dec = b2 + a21 * obj_x + a22 * obj_y
    
    return [ra, dec]

## Estimate the orbit of the object using MCMC
We will go over this in lecture.

In [ ]:
ra1, dec1 = 347.67944091/180*np.pi,  14.13233392/180*np.pi #rad
ra2, dec2 = 347.67524986/180*np.pi,  14.13235671/180*np.pi
dt = 1+12/60 # hour
dra1 = (ra2-ra1)/dt * 24 * 365.25 / (np.pi*2)   # rad/(year/2pi)
ddec1 = (dec2-dec1)/dt * 24 * 365.25 / (np.pi*2)

In [ ]:
sim = rebound.Simulation()
sim.add(["Sun","Earth", "Kleopatra"], date="2022-08-11 03:14:00", plane="frame")

In [ ]:
rebound.OrbitPlot(sim)

In [ ]:
def logl(par):
    a, l, h, k, ix, iy = par
    
    # simple prior
    if a<1 or a>4 or h<-0.5 or h>0.5 or k<-0.5 or k>0.5 or ix<-0.5 or ix>0.5 or iy<-0.5 or iy>0.5 :
        return -np.inf
    
    # relative particle position
    p_p = rebound.Particle(simulation=sim,a=a, l=l,h=h,k=k,ix=ix,iy=iy) 
    p = p_p- sim.particles[1] 
    x, y,z = p.xyz
    
    # Predict ra, dec, and derivatives
    ra = np.arctan2(y,x)%(np.pi*2.)
    dra = -y/(x**2+y**2) * p.vx + x/(x**2+y**2) * p.vy
    
    dec = np.arctan2(z,np.sqrt(x**2+y**2))
    ddec = -z/(x**2+y**2+z**2) /np.sqrt(x**2+y**2) * (p.x*p.vx + p.y*p.vy) + \
           np.sqrt(x**2+y**2)/(x**2+y**2+z**2) * p.vz
    
    # return log likelihood
    l = 0
    l += (ra-ra1)**2 / 0.00001**2  # rough estimates of accuracy (you should improve this!)
    l += (dec-dec1)**2 / 0.00001**2
    l += (dra-dra1)**2 / (0.00001 * 24 * 365.25 / (np.pi*2))**2 
    l += (ddec-ddec1)**2 / (0.00001 * 24 * 365.25 / (np.pi*2))**2 
    return -l


In [ ]:
nwalkers, ndim = 40, 6

# initial conditions close to true values
o = sim.particles[2].orbit()
pos_t = np.array([o.a, o.l, o.pal_h, o.pal_k, o.pal_ix, o.pal_iy])
pos = pos_t + 1e-5*np.random.randn(nwalkers,ndim)

In [ ]:
# run mcmc
sampler = emcee.EnsembleSampler(nwalkers, ndim, logl)
sampler.run_mcmc(pos, 500_000, progress=True);

In [ ]:
# Check if semi-major axes are converged
samples = sampler.get_chain(thin=100)
f, a = plt.subplots(1,1)
a.plot(samples[:,:,0]);

In [ ]:
s = sampler.get_chain(flat=True,thin=1)
sn = np.zeros((s.shape[0],3))
for i, par in enumerate(s):
    a, l, h, k, ix, iy = par
    e = np.sqrt(h**2+k**2)
    inc = np.sqrt(ix**2+iy**2)
    sn[i] = [a, e, inc]

In [ ]:
# corner plot with true values
fig = corner.corner(sn, labels=["a","e","inc"],truths=[sim.particles[2].a,sim.particles[2].e,sim.particles[2].inc]);

In [ ]:
# Draw a few samples
s = sampler.get_chain(flat=True,thin=300000)
sim2 = sim.copy()
for par in s:
    a, l, h, k, ix, iy = par
    sim2.add(a=a, l=l,h=h,k=k,ix=ix,iy=iy) 
rebound.OrbitPlot(sim2)